In [ ]:
import os,re,time,json,sys

"""
"/模板文件"目录下 课时划分.txt 与 课时目标及单元目标.txt 文件不能缺失
"""

"""---设置文件名---"""
#目录和文件的分隔务必用/
lessoncut_file = "临时文件/按课时分类目标及题目清单" 
lessonobj_file = "临时文件/课时目标及单元目标表" 
"""---设置文件名结束---"""

#读取系统日期
current_time = time.localtime()
time_string = "_"+str(current_time.tm_year).zfill(4)+str(current_time.tm_mon).zfill(2)+str(current_time.tm_mday).zfill(2)


lessoncut_file +=  time_string +".tex"
lessonobj_file +=  time_string +".tex"


#读取题库json文件并转化为字典
with open(r"../题库0.3/Problems.json","r",encoding = "utf8") as f:
    database = f.read()
pro_dict = json.loads(database)

#读取目标数据库json并转化为字典
with open(r"../题库0.3/LessonObj.json","r",encoding = "utf8") as f:
    database = f.read()
lessonobj_dict = json.loads(database)

#读取课时数据库json并转化为字典
with open(r"../题库0.3/LessonsCut.json","r",encoding = "utf8") as f:
    database = f.read()
lessoncut_dict = json.loads(database)

#读取单元目标数据库json并转化为字典
with open(r"../题库0.3/UnitObj.json","r",encoding = "utf8") as f:
    database = f.read()
unitobj_dict = json.loads(database)

#以下是课时题目统计
#生成单元课时列表(Kddll)
lessons_descr = [] 
for o in lessonobj_dict:
    if not o[:5] in lessons_descr:
        lessons_descr.append(o[:5])
lessons_dict = {}
lessons_string = ""
for l in lessons_descr:
    lessons_dict[l] = [0,""]
for p in pro_dict:
    for l in lessons_descr:
        for o in pro_dict[p]["objs"]:
            if l in o:
                lessons_dict[l][0] += 1
                lessons_dict[l][1] += p + ","
                break
#lessons_string是简要列表, lessons_dict是详细清单
for l in lessons_descr:
    lessons_string += l + ": " + str(lessons_dict[l][0]) + "\n" 
#课时统计完成

#以下是目标题目统计
objs_dict = {}
objs_string = ""
for o in lessonobj_dict:
    objs_dict[o] = [0,""]
for p in pro_dict:
    for o in lessonobj_dict:
        if o in pro_dict[p]["objs"]:
            objs_dict[o][0] += 1
            objs_dict[o][1] += p + ","
# objs_string是简要列表, objs_dict是详细清单
for o in lessonobj_dict:
    objs_string += o + ": " + str(objs_dict[o][0]) + "\n" 
#课时统计完成

#生成课时目标汇总的latex文件内容lessons_obj_string, 准备放到latex文件中
lessons_obj_string = ""
for obj in lessonobj_dict:
    lessons_obj_string += lessonobj_dict[obj]["id"] + " & " + lessonobj_dict[obj]["unit_obj"] + " & " + lessonobj_dict[obj]["content"] + r"\\ \hline" + "\n"   

#生成单元目标汇总的latex文件内容units_obj_string, 准备放到latex文件中
units_obj_string = ""
for obj in unitobj_dict:
    units_obj_string += unitobj_dict[obj]["id"] + "&" + unitobj_dict[obj]["content"] + r"\\ \hline" + "\n"

#生成课时统计的latex文件内容lessons_cut_string, 准备放到latex文件中
lessons_cut_string = ""
for lesson in lessons_dict:
    unit_index = lesson[1:3]
    lesson_index = lesson[3:5]
    lessons_cut_string += r"\section*{第" + unit_index + "单元, 第" + lesson_index +r"课时}"+ "\n\n"
    lessons_cut_string += r"起始页码: " + lessoncut_dict[lesson]["start"] + "; 终止页码: " + lessoncut_dict[lesson]["end"] + ".\n\n"
    lessons_cut_string += r"\begin{itemize}" + "\n\n"
    for o in lessonobj_dict:
        if lesson in o:
            lessons_cut_string +=  r"\item " + o + "|" + lessonobj_dict[o]["unit_obj"] + "|" + lessonobj_dict[o]["content"] + "\n\n"
            lessons_cut_string += "关联题目数: " + str(objs_dict[o][0]) + ". 列表: " + objs_dict[o][1].replace(",",", ") + "\n\n"
    lessons_cut_string += r"\item 课时汇总" + "\n\n" + "本课时总题目数: " + str(lessons_dict[lesson][0]) + ".\n\n" + "列表: " +  lessons_dict[lesson][1].replace(",",", ") + "\n\n"
    lessons_cut_string += r"\end{itemize}" + "\n\n"


#替换单元课时目标的latex文件的内容并编译
with open("模板文件/课时目标及单元目标.txt","r",encoding = "utf8") as f:
    obj_latex_file_raw = f.read()
#识别操作系统
if sys.platform != "win32":
    obj_latex_file_raw = re.sub(r"fontset[\s]*=[\s]*none","fontset = fandol",obj_latex_file_raw)
    obj_latex_file_raw = re.sub(r"\\setCJKmainfont",r"% \\setCJKmainfont",obj_latex_file_raw)
obj_latex_file_new = obj_latex_file_raw.replace("课时目标待替换",lessons_obj_string).replace("单元目标待替换",units_obj_string)
with open(lessonobj_file,"w",encoding = "utf8") as f:
    f.write(obj_latex_file_new)
print("开始编译单元与课时目标信息pdf文件:", lessonobj_file)
d = re.search("/[^/]*$",lessonobj_file).span()[0]
lessonobj_dir = lessonobj_file[:d]
os.system("xelatex -interaction=batchmode -output-directory=" + lessonobj_dir + " "+ lessonobj_file)
os.system("xelatex -interaction=batchmode -output-directory=" + lessonobj_dir + " "+ lessonobj_file)

#替换课时划分的latex文件的内容并编译
with open("模板文件/课时划分.txt","r",encoding = "utf8") as f:
    lessons_cut_latex_file_raw = f.read()
#识别操作系统
if sys.platform != "win32":
    lessons_cut_latex_file_raw = re.sub(r"fontset[\s]*=[\s]*none","fontset = fandol",lessons_cut_latex_file_raw)
    lessons_cut_latex_file_raw = re.sub(r"\\setCJKmainfont",r"% \\setCJKmainfont",lessons_cut_latex_file_raw)
lessons_cut_latex_file_new = lessons_cut_latex_file_raw.replace("待替换",lessons_cut_string)
with open(lessoncut_file,"w",encoding = "utf8") as f:
    f.write(lessons_cut_latex_file_new)
print("开始编译课时划分信息pdf文件:", lessoncut_file)
d = re.search("/[^/]*$",lessoncut_file).span()[0]
lessoncut_dir = lessoncut_file[:d]
os.system("xelatex -interaction=batchmode -output-directory=" + lessoncut_dir + " "+ lessoncut_file)
os.system("xelatex -interaction=batchmode -output-directory=" + lessoncut_dir + " "+ lessoncut_file)

print("已输出至pdf文件",r"临时文件/课时目标及单元目标表","及",r"临时文件/按课时分类目标及题目清单")


开始编译单元与课时目标信息pdf文件: 临时文件/课时目标及单元目标表_20230221.tex
开始编译课时划分信息pdf文件: 临时文件/按课时分类目标及题目清单_20230221.tex


0